In [10]:
import matplotlib.pyplot as plt
import numpy as np
import random
import time  # Importing the time module to measure execution time

We here built on the extended 3-state model introduced in the lecture. This model contains one additional feature, which lets you choose between 3 different spreading modes. Besides the global spreading (spreading_mode = 0), where a recruiting nucleosome n1 and a substrate nucleosome n2 are chosen randomly, and the nearest-neighbor spreading (spreading_mode = 1), where n1 is chosen randomly and n2 as a nearest neighbor, this model version contains an additional cooperative, global spreading mode (spreading_mode = 2), where two recruiting nucleosomes n1 and n2  and a substrate nucleosome n3 are all chosen randomly. This allows you to answer Question 4 of Problem Set #4 - chromatin and epigenetics.

In [13]:
def extended_recruitment_model(N, alpha, states, spreading_mode, n):
    #generate nucleosome array of size N with randomly distributed nucleosome states A (0), U (1), and M(2)
    DNA_region = np.random.randint(0,states,N)
    #determine the number of timesteps for the whole timecourse
    duration = N*4000
    #
    A_timecourse = np.zeros(duration)
    U_timecourse = np.zeros(duration)
    M_timecourse = np.zeros(duration)

    # count the number of nucleosomes that are initially in state A
    A_timecourse[0] = np.count_nonzero(DNA_region==0)
    
    if states == 3:
        # count the number of nucleosomes that are initially in state U
        U_timecourse[0] = np.count_nonzero(DNA_region==1)
        # count the number of nucleosomes that are initially in state M
        M_timecourse[0] = np.count_nonzero(DNA_region==2)
    elif states == 2:
        # count the number of nucleosomes that are initially in state M
        M_timecourse[0] = np.count_nonzero(DNA_region==1)

    #create time_space_matrix
    time_space_matrix = np.zeros([duration, N])
    #store initial state of nucleosomes in matrix
    time_space_matrix[0] = DNA_region
    
    for t in range(duration):
        #generate a random real number between 0 and 1
        ran1 = np.random.random(1)[0]
        # with probability alpha, do a recruited conversion attempt
        if alpha > ran1:
            #select a random recruiting nucleosome from the DNA region
            n1 = np.random.randint(N)
            
            if spreading_mode == 0:
                #select a random substrate nucleosome from the DNA region
                n2 = np.random.randint(N)
            elif spreading_mode == 1:
                #select a random substrate nucleosome from the DNA region
                ran2= np.random.random(1)[0]
                if ran2 < 0.5 and n1!=0:
                    n2 = n1-1
                elif ran2 > 0.5 and n1!=N-1:
                    n2 = n1+1
            elif spreading_mode == 2:
                #select a random substrate nucleosome from the DNA region
                n2 = np.random.randint(N)
                n3 = np.random.randint(N)
                
            # if the recruiting nucleosome is in A state, but the substrate nucleosome is not
            if DNA_region[n1] == 0 and DNA_region[n2] != 0 and spreading_mode != 2:
                    # change state of substrate nucleosome one step towards A
                    DNA_region[n2] -= 1
                
            # if the recruiting nucleosome is in M state, but the substrate nucleosome is not
            elif DNA_region[n1] == states-1 and DNA_region[n2] != states-1 and spreading_mode != 2:
                    # change state of substrate nucleosome one step towards A
                    DNA_region[n2] += 1

            elif spreading_mode == 2 and DNA_region[n1] == 0 and DNA_region[n2] == 0 and DNA_region[n3] != 0:
                    DNA_region[n3] -= 1
                
            elif spreading_mode == 2 and DNA_region[n1] == states-1 and DNA_region[n2] == states-1 and DNA_region[n3] != states-1:
                    DNA_region[n3] += 1

                
                
        # with probability 1-alpha, do a noisy conversion attempt
        else:
            # pick a random nucleosome
            ran3 = np.random.random(1)[0]
            n3 = np.random.randint(N)
            # with 1/3 probability, change the state to A (decrease state)
            if ran3 < 1/3:
                if DNA_region[n3] != 0:
                    DNA_region[n3] -= 1
            # with 1/3 probability, change the state to M (increase state)
            elif ran3 > 2/3:
                if DNA_region[n3] != states-1:
                    DNA_region[n3] += 1
            

        A_timecourse[t] = np.count_nonzero(DNA_region==0)
        
        if states == 3:
            # count the number of nucleosomes that are initially in state U
            U_timecourse[t] = np.count_nonzero(DNA_region==1)
            # count the number of nucleosomes that are initially in state M
            M_timecourse[t] = np.count_nonzero(DNA_region==2)
        elif states == 2:
            # count the number of nucleosomes that are initially in state M
            M_timecourse[t] = np.count_nonzero(DNA_region==1)

        time_space_matrix[t] = DNA_region
        
        #Simulate DNA replication after n average conversion attempts per nucleosome
        if n!=0 and t%(N*n) == 0:
            for i in range(N):
                ran4 = np.random.random(1)[0]
                if ran4 < 0.5:
                    DNA_region[i] = states-2
                


    return(A_timecourse, U_timecourse, M_timecourse, time_space_matrix)
        
        

# Chose 5 parameter values below

In [21]:
# determine a system size (number of nucleosomes) (range between 30 and 120)
N = 60
# determine a value for alpha (recruited conversion attempt rate), which is a real number between 0 and 1
alpha = 0.75
# number of nucleosome states (choose either 2 or 3)
states = 3
# global spreading (spreading_mode = 0) and nearest neighbor spreading (spreading_mode = 1) or cooperative, global spreading mode 
# (spreading_mode = 2)
spreading_mode = 0
# generation time (number of time-steps between DNA replication; 0 means no DNA replication is simulated)
n = 0

# The code below executes the extended_recruitment_model function and generates the output

In [ ]:
# Start timing
start_time = time.time()
# Call the recruitment_model function
A_timecourse, U_timecourse, M_timecourse, time_space_matrix = extended_recruitment_model(N, alpha, states, spreading_mode, n)

# End timing
end_time = time.time()
# Print the execution time
print(f"Execution time: {end_time - start_time} seconds")

# Create a figure with two subplots
fig, axs = plt.subplots(2, 1, figsize=(6, 8))  # Adjust height to make room for both plots

# First subplot for A_timecourse
axs[0].plot(M_timecourse)
axs[0].set_yticks([0,1/4*N,2/4*N,3/4*N,N], labels=[0,1/4*N,2/4*N,3/4*N,N], fontsize=12)
axs[0].set_xticks([1000*N, 2000*N, 3000*N, 4000*N], labels=[1000, 2000, 3000, 4000], fontsize=12)
#axs[0].set_xlabel("Time (average conversion attempts per nucleosome)", fontsize=15)
axs[0].set_ylabel("Number of M nucleosomes", fontsize=15)
axs[0].set_xlim([0,4000*N])

# Second subplot for the space_time plot
time_space_matrix_condensed = time_space_matrix[0:N*4000:N*40]
rows, cols = time_space_matrix_condensed.shape

# Loop through the data and plot circles with the specified colors
for i in range(rows):
    for j in range(cols):
        value = time_space_matrix_condensed[i, j]
        if value == 0:
            color = 'blue'  # Color for value 1
        elif value == 1 and states == 2:
            color = 'red'  # Color for value 0
        elif value == 1 and states == 3:
            color = 'lightgrey'  # Color for value 0
        elif value == 2 and states == 3:
            color = 'red'  # Color for value 0
        else:
            continue  # Skip any other values

        circle = plt.Circle((i, j), 0.25, color=color)  # Adjust radius as needed
        axs[1].add_artist(circle)

# Set limits and aspect for the second subplot
axs[1].set_xlim(-0.5, rows - 0.5)  # Adjust limits for rotated view
axs[1].set_ylim(-0.5, cols - 0.5)
#axs[1].set_aspect('equal')
axs[1].set_xticks([25, 50, 75, 100], labels=[40*25, 40*50, 40*75, 40*100], fontsize=12)
axs[1].set_yticks([0,1/4*N,2/4*N,3/4*N,N], labels=[0,1/4*N,2/4*N,3/4*N,N], fontsize=12)
axs[1].set_xlabel('Time (average conversions per nucleosome)', fontsize=15)
axs[1].set_ylabel('Nucleosome position', fontsize=15)

# Show the plot
plt.tight_layout()  # Adjust layout to prevent overlap
plt.show()

Execution time: 2.7366549968719482 seconds
